# Biomass Yield and Spectral Trends

```
date: 2024-12-12
authors:
    - name: Brookie Guzder-Williams
affiliations:
    - University of California Berkeley, The Eric and Wendy Schmidt Center for Data Science & Environment
license: CC-BY-4.0
```

This notebook uses DSE's [Spectral Trend Database](https://github.com/SchmidtDSE/spectral_trend_database) (STDB) to
produce and interactive chart displaying Biomass Yield vs a number of different spectral incides over time.

1. Fetch Data for a random point: We use STDS's [query module](https://github.com/SchmidtDSE/spectral_trend_database/blob/main/spectral_trend_database/query.py) and in particular the [`QueryConstructor`](https://github.com/SchmidtDSE/spectral_trend_database/blob/54146cf058e2180829e2c169b37c18ddf62b68a0/spectral_trend_database/query.py#L21-L114) to generate a ...
2. Build Chart
3. Save Chart JSON to improve responsiveness of chart


---

### IMPORTS


In [1]:
from importlib import reload
from typing import Callable, Union, Optional, Literal, TypeAlias, Sequence, Any
import re
from pprint import pprint
import random
import pandas as pd
import numpy as np
import xarray as xr
import tensorflow as tf
from IPython.display import HTML
import matplotlib.pyplot as plt
import seaborn as sns
import altair as alt
from spectral_trend_database.config import config as c
from spectral_trend_database import query
from spectral_trend_database import utils
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import HistGradientBoostingClassifier
from sklearn import metrics


---

### CONFIG

In [2]:
BQ_PREFIX = 'dse-regenag.BiomassTrends'
SAMPLE_FRAC = 0.0005
YEAR_START = 2008
YEAR_END = 2020
START_MMDD = '11-01'
END_MMDD = START_MMDD
ATTR_COLS = [
    'sample_id',
    'lon',
    'lat']
LIST_ATTRS = [
    'year',
    'biomass',
    'crop_type']
CHART_DATA_PATH = 'spectral_trends.chart_data.json'


---

### HELPER METHODS


In [3]:
def print_list(lst, max_len=7, view_size=3, sep=', ', connector=' ... '):
    size = len(lst)
    if size <= max_len:
        lst_str = sep.join(lst)
    else:
        head = sep.join(lst[:view_size])        
        tail = sep.join(lst[-view_size:])
        lst_str = f'{head}{connector}{tail}  [{size}]'
    print(lst_str)

def line(marker='-', length=100):
    print(marker*length)


---

### STDB DATABASE INFO

First we'll take a quick peak at the what is in the STDB database

In [4]:
YIELD_TABLE = 'SCYM_YIELD'
SMOOTHED_INDICES_TABLE = 'SMOOTHED_INDICES_V1'
IDENT_DATE_COLUMNS = ['sample_id', 'year', 'date']

In [5]:
COLUMN_NAMES = {}
print('DATABASE INFO')
line()
query = reload(query)
table_names = query.table_names()
print('TABLES:')
pprint(table_names)
for table_name in [YIELD_TABLE, SMOOTHED_INDICES_TABLE]:
    COLUMN_NAMES[table_name] = query.column_names(table_name, run_query=True)
    print(f'\n{table_name}:')
    print_list(COLUMN_NAMES[table_name])
line()

DATABASE INFO
----------------------------------------------------------------------------------------------------
TABLES:
['SMOOTHED_INDICES_V1',
 'INDICES_STATS_V1',
 'LANDSAT_RAW_MASKED',
 'RAW_INDICES_V1',
 'SAMPLE_POINTS',
 'INDICES_STATS_V1_GROWING_SEASON',
 'INDICES_STATS_V1_OFF_SEASON',
 'ADMINISTRATIVE_BOUNDARIES',
 'SCYM_YIELD',
 'MACD_INDICES_V1']

SCYM_YIELD:
biomass, crop_type, year, sample_id

SMOOTHED_INDICES_V1:
ndbr, ndvi, grvi ... sample_id, rdvi, year  [39]
----------------------------------------------------------------------------------------------------


In [6]:
INDICES = [c for c in COLUMN_NAMES[SMOOTHED_INDICES_TABLE] if c not in IDENT_DATE_COLUMNS]
print_list(INDICES)

ndbr, ndvi, grvi ... si, nli, rdvi  [36]



---

### 1. Fetch Data

In [7]:
qc = query.QueryConstructor('SAMPLE_POINTS', table_prefix=BQ_PREFIX)
qc.select('sample_id')
qc.append(f'WHERE RAND() < {SAMPLE_FRAC}')
sample_ids_df = query.run(sql=qc.sql(), print_sql=True)
sample_ids_df = sample_ids_df.drop_duplicates()
print('nb_samples:', sample_ids_df.shape[0])

[info] spectral_trend_database.query.run: SELECT sample_id FROM `dse-regenag.BiomassTrends.SAMPLE_POINTS` WHERE RAND() < 0.0005
nb_samples: 11


In [8]:
def fetch_yield_and_trend_data(
        year_start: int,
        year_end: Optional[int] = None,
        sample_id: Optional[Union[list[str], str]] = None,
        print_sql: Optional[bool] = False,
        limit: Optional[int] = None) -> pd.DataFrame:
    """
    Builds and Executes a SQL Query to get all data
    form a given set of sample_ids during a specified time 
    period.
    
    Args: 
        year_start (int): start year to select data
        year_end (Optional[int] = None): 
            last year to select data from (inclusive). if None use <year_start>
        sample_id (Optional[Union[list[str], str]] = None)
            sample_id or list of sample-ids of data to select. if none select 
            from all samples.
        print_sql (Optional[bool] = False)
        limit (Optional[int] = None)

    Returns:
        pd.DataFrame of smoothed-spectral-indices
    """
    if year_end is None: 
        year_end=year_start
    qc = query.QueryConstructor(
        'SAMPLE_POINTS', 
        table_prefix=BQ_PREFIX,
        using=['sample_id'],  
        how='inner')
    qc.join('SCYM_YIELD')
    qc.join('SMOOTHED_INDICES_V1', 'sample_id', 'year')
    if sample_id:
        if isinstance(sample_id, list):
            sample_id = [f"'{s}'" for s in sample_id]
            sample_ids = f'({", ".join(sample_id)})'
            qc.where(sample_id=sample_ids, sample_id_op='in')
        else:
            qc.where(sample_id=sample_id)
    qc.where('SMOOTHED_INDICES_V1', year=year_start, year_op='>=')
    qc.where('SMOOTHED_INDICES_V1', year=year_end, year_op='<=')
    df = query.run(sql=qc.sql(), print_sql=print_sql)
    return df

In [9]:
data = fetch_yield_and_trend_data(
    year_start=YEAR_START,
    year_end=YEAR_END,
    sample_id=sample_ids_df.sample_id.tolist(),
    print_sql=True)

print('shape:', data.shape)
data.sample(3)

[info] spectral_trend_database.query.run: SELECT * FROM `dse-regenag.BiomassTrends.SAMPLE_POINTS` INNER JOIN `dse-regenag.BiomassTrends.SCYM_YIELD` USING (sample_id) INNER JOIN `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1` USING (sample_id, year) WHERE `dse-regenag.BiomassTrends.SAMPLE_POINTS`.sample_id in ('9zkdxj8uqs9', '9zmqe6x1qvx', '9zr0vxc7v23', '9zs7xnz5hd2', '9zw2q867xge', 'dn9nxvsxzqj', 'dp0ecwwerw1', 'dp172wg7xbh', 'dp4w1ehxc0h', 'dp4z41fcb3c', 'dp76uqq473h') AND `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1`.year >= 2008 AND `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1`.year <= 2020
shape: (137, 46)


sample_id  year geohash_5 geohash_7  geohash_9        lon        lat  \
82   dp0ecwwerw1  2020     dp0ec   dp0ecww  dp0ecwwer -89.221707  40.070476   
26   9zr0vxc7v23  2018     9zr0v   9zr0vxc  9zr0vxc7v -91.162607  40.956304   
134  dp76uqq473h  2015     dp76u   dp76uqq  dp76uqq47 -85.234535  41.299373   

     biomass crop_type                                               ndbr  \
82      2484      corn  [0.41572691343154944, 0.4216905623897893, 0.42...   
26       822       soy  [0.5380786514290266, 0.5589752424971657, 0.576...   
134      763       soy  [0.7431992255247601, 0.7039935848746685, 0.666...   

     ...                                                msr  \
82   ...  [-0.21862459707548487, -0.08483681438869617, 0...   
26   ...  [2.006944590386502, 2.0055490358359256, 1.9992...   
134  ...  [1.7063325740949453, 1.6207742081728391, 1.538...   

                                                   tvi  \
82   [0.7715223744950364, 0.7991606443015192, 0.825...   
26   [0.9232387788591468, 0.9531902681348432, 0.980...   
134  [1.1677720600108652, 1.153969758930652, 1.1404...   

                                                   si1  \
82   [0.4917605423131759, 0.4555494881499426, 0.421...   
26   [0.5553325922342004, 0.5017862539211081, 0.451...   
134  [0.06001421396453435, 0.06027281235105134, 0.0...   

                                                   rvi  \
82   [-0.5428972357175993, -0.008500791658871187, 0...   
26   [10.522622757491767, 10.29771701716179, 10.066...   
134  [6.73106052007628, 6.399464052866614, 6.082262...   

                                                  tdvi  \
82   [0.21095737232990322, 0.2403358404543997, 0.26...   
26   [0.43910674352768286, 0.4605788461275002, 0.47...   
134  [0.6459509395919975, 0.6116532427291639, 0.579...   

                                                 osavi  \
82   [0.09165915248813342, 0.12732055482016302, 0.1...   
26   [0.4233851930987115, 0.44576605410974524, 0.46...   
134  [0.6232193270663787, 0.5961589986937039, 0.570...   

                                                    si  \
82   [0.48094651430259516, 0.4451493185554874, 0.41...   
26   [0.5503076516430196, 0.4957181783427678, 0.444...   
134  [0.05792541330470242, 0.0576103634843892, 0.05...   

                                                   nli  \
82   [-0.16355058802918726, -0.1217022671484878, -0...   
26   [0.5376847091595586, 0.5485060271373918, 0.554...   
134  [0.6678533099625199, 0.5856441129559676, 0.507...   

                                                  date  \
82   [2019-09-13T00:00:00.000000000, 2019-09-14T00:...   
26   [2017-09-05T00:00:00.000000000, 2017-09-06T00:...   
134  [2014-09-09T00:00:00.000000000, 2014-09-10T00:...   

                                                  rdvi  
82   [0.14149805433615034, 0.16919856340731884, 0.1...  
26   [0.38007294799131586, 0.39915820223195475, 0.4...  
134  [0.550739097205325, 0.525267989739944, 0.50092...  

[3 rows x 46 columns]

In [10]:
rows = data[data.sample_id == data.sample().sample_id.iloc[0]]
rows = rows.sort_values('year').reset_index(drop=True)

In [11]:
utils = reload(utils)
def filter_dates(row):
    return dict(date=slice(f'{row.year-1}-{START_MMDD}', f'{row.year}-{END_MMDD}'))
    
ds = utils.rows_to_xr(
    rows, 
    coord='date', 
    sel=filter_dates, 
    attr_cols=ATTR_COLS,
    list_attrs=LIST_ATTRS)
ds

<xarray.Dataset>
Dimensions:   (date: 4390)
Coordinates:
  * date      (date) datetime64[ns] 2007-11-01 2007-11-02 ... 2019-11-01
Data variables: (12/36)
    ndbr      (date) float64 0.1402 0.1386 0.137 0.1354 ... 0.4119 0.416 0.4215
    ndvi      (date) float64 0.2034 0.2045 0.2056 0.2067 ... 0.2406 0.228 0.2152
    grvi      (date) float64 1.757 1.778 1.799 1.82 ... 2.19 2.116 2.042 1.97
    ndwi      (date) float64 -0.2676 -0.2728 -0.278 ... -0.3169 -0.3025 -0.2883
    slavi     (date) float64 0.7055 0.7051 0.7048 0.7044 ... 0.979 0.9619 0.9462
    ndmi      (date) float64 -0.0294 -0.03497 -0.04057 ... 0.2404 0.251 0.2627
    ...        ...
    rvi       (date) float64 1.508 1.512 1.516 1.52 ... 1.72 1.667 1.616 1.566
    tdvi      (date) float64 0.1767 0.1746 0.1725 0.1703 ... 0.1954 0.193 0.1901
    osavi     (date) float64 0.1535 0.1534 0.1533 0.1532 ... 0.1664 0.16 0.1535
    si        (date) float64 0.1867 0.1814 0.1761 ... 0.2644 0.2796 0.2947
    nli       (date) float64 -0.3615 -0.3697 -0.378 ... -0.2579 -0.248 -0.2384
    rdvi      (date) float64 0.1469 0.1459 0.145 0.1441 ... 0.1668 0.1627 0.1582
Attributes:
    sample_id:  9zkdxj8uqs9
    lon:        -94.6129475242
    lat:        41.2516700194
    year:       [2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, ...
    biomass:    [647, 2389, 807, 2243, 548, 1860, 785, 2711, 839, 2554, 759, ...
    crop_type:  ['soy', 'corn', 'soy', 'corn', 'soy', 'corn', 'soy', 'corn', ...

In [12]:
yield_biomass = { y: b for y,b in zip(ds.year, ds.biomass)}
crop_types = { y: b for y,b in zip(ds.year, ds.crop_type)}
dvars = { k: ds[k].data for k in ds.data_vars }
_df = pd.DataFrame(dvars)
_df['date'] = ds.date.data
_df['idx'] = list(_df.index)
_df['year'] = _df.date.apply(lambda d: d.year)
_df['biomass'] = _df.year.apply(lambda y: yield_biomass.get(y, None))
_df['crop_type'] = _df.year.apply(lambda y: crop_types.get(y, 'soy'))

In [13]:
_df.date.astype(str)

0       2007-11-01
1       2007-11-02
2       2007-11-03
3       2007-11-04
4       2007-11-05
           ...    
4385    2019-10-28
4386    2019-10-29
4387    2019-10-30
4388    2019-10-31
4389    2019-11-01
Name: date, Length: 4390, dtype: object

In [14]:
# _df['date'] = _df.date.astype(str).apply(lambda d: f'{d}T00:00:01.000Z')
# _df['date'] = pd.to_datetime(_df.date.astype(str))
# _df.to_json(CHART_DATA_PATH, orient='records', lines=False)


---

### CHART

In [15]:
S = 1.25
DEFAULT_INDEX = 'ndvi'
HEIGHT = 400 * S
GRAPH_WIDTH = 600 * S
SI_COLOR = '#515e68'
SI_OPACITY = 0.6
YIELD_OPACITY = 0.5
TITLE_COLOR = '#333'
TITLE_SIZE = 22
TITLE_WEIGHT = 200
SUBTITLE_COLOR = '#aaa'
SUBTITLE_SIZE = 14
SOY_COLOR = '#4e9561'
CORN_COLOR = '#e2d644'

In [16]:
TITLE = 'SPECTRAL TRENDS'
SUBTITLE = 'exploring yield as a function of spectral indices'

In [17]:
chart_data = _df
# chart_data = CHART_DATA_PATH

In [18]:
#| label: nb.indices_vs_yield
#| placeholder: ./images/TBD.png

# alt.data_transformers.enable("vegafusion")

display(HTML("""
<style>
  span.vega-bind-name {
    color: #555;
    margin: 0 10px 0 60px;
    font-size: 20px;
  }
  .vega-bind label select {
    color: #555;
    font-size: 18px;
  }
</style>
"""))

# yield chart
yield_scale = alt.Scale(
    domain=[0.0, 3000],
    clamp=True
)
yield_color_scale = alt.Scale(
    domain=['soy', 'corn'], 
    range=[SOY_COLOR, CORN_COLOR])
yield_yaxis = alt.Axis(title='Biomass Yield', titleFontSize=18, titleColor=TITLE_COLOR, titleFontWeight=TITLE_WEIGHT)
yield_chart = alt.Chart(chart_data).encode(
    x=alt.X('date:T', title=None),
    y=alt.Y('biomass:Q', axis=yield_yaxis, scale=yield_scale),
    color=alt.Color('crop_type:N', scale=yield_color_scale)
).mark_area(
    filled=True,
    opacity=YIELD_OPACITY,
    interpolate='step-before')

# interactive spectral index chart
si_yaxis = alt.Axis(title='Spectral Index', titleFontSize=18, titleColor=TITLE_COLOR, titleFontWeight=TITLE_WEIGHT)
si_dropdown = alt.binding_select(
    options=INDICES,
    labels=[n.upper() for n in INDICES],
    name='Spectral Index: '.upper()
)
ycol_param = alt.param(
    value=DEFAULT_INDEX,
    bind=si_dropdown
)
si_chart = alt.Chart(chart_data).encode(
    x=alt.X('date:T', title=None),
    y=alt.Y('y:Q', axis=si_yaxis)
).properties(
    width=GRAPH_WIDTH,
    height=HEIGHT
).transform_calculate(
    y=f'datum[{ycol_param.name}]'
).add_params(
    ycol_param
).mark_area(
    fill=SI_COLOR,
    fillOpacity=SI_OPACITY
)

# display
title = alt.Title(
    TITLE,
    color=TITLE_COLOR,
    fontSize=TITLE_SIZE,
    fontWeight=TITLE_WEIGHT,
    subtitle=SUBTITLE,
    subtitleColor=SUBTITLE_COLOR,
    subtitleFontSize=SUBTITLE_SIZE)

chart = alt.layer(yield_chart, si_chart).resolve_scale(y='independent')
chart = chart.properties(
    title=title).configure_legend(
    title=None,
    labelFontSize=18,  
    labelColor=SUBTITLE_COLOR 
).interactive()
chart 

alt.LayerChart(...)